# Team 6 Project: MINJUSTICIA

In [1]:
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from lifelines import KaplanMeierFitter
from lifelines.statistics import logrank_test
from scipy import stats
import plotly.graph_objects as go
from plotly.offline import init_notebook_mode, iplot
from plotly.graph_objs import *
init_notebook_mode(connected=True) 
import plotly.express as px

path = "C:/Users/david/Desktop/ds4a-team6/retomintic/Data_UpdateJune13/reincidencia11junio2020_clean.csv"
df_mj = pd.read_csv(path, sep=",",encoding="utf-8")

C:\Users\david\AppData\Local\Continuum\anaconda3\lib\site-packages\statsmodels\tools\_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [2]:
#Date variables are parsed to datetime
df_mj["FECHA_CAPTURA"] = pd.to_datetime(df_mj["FECHA_CAPTURA"])
df_mj["FECHA_INGRESO"] = pd.to_datetime(df_mj["FECHA_INGRESO"])
df_mj["FECHA_SALIDA"] = pd.to_datetime(df_mj["FECHA_SALIDA"])
#Month and year variables are defined
df_mj["MES_INGRESO_INT"]=df_mj["FECHA_INGRESO"].dt.strftime('%m')
df_mj["ANO_INGRESO_INT"]=df_mj["FECHA_INGRESO"].dt.strftime('%y')
#Calculations on how much time have the criminal being outside since its last stay in jail
for column in ['FECHA_INGRESO', 'FECHA_SALIDA', 'FECHA_CAPTURA']:
    df_mj = df_mj.sort_values(['INTERNOEN', column], ascending = False)
    
    df_mj['DIAS' + column[5:]] = -1*(df_mj[column].diff()/timedelta(days = 1))

    df_mj.loc[(df_mj.INTERNOEN != df_mj.INTERNOEN.shift(1)) | (df_mj['DIAS' + column[5:]] == 0), 
              ['DIAS' + column[5:]]] = (datetime.today() - df_mj[column])/timedelta(days = 1)
    
#It seems that sometimes entering and gettint out is switched, that's why we computed in absolute values
df_mj['DIAS_CONDENA'] = abs(df_mj['FECHA_SALIDA'] - df_mj['FECHA_INGRESO'])/timedelta(days = 1)
df_mj['DIAS_JUDICIALIZACION'] = df_mj['FECHA_INGRESO'] - df_mj['FECHA_CAPTURA']
df_mj['DIAS_LIBRE'] = df_mj['DIAS_INGRESO'] - df_mj['DIAS_CONDENA']
#The individual finishes its sentence but she's incarcelated inmediately for another crime
df_mj.loc[df_mj.DIAS_CAPTURA < 0, 'DIAS_CAPTURA'] = 0
df_mj.loc[df_mj.DIAS_INGRESO < 0, 'DIAS_INGRESO'] = 0
df_mj.loc[df_mj.DIAS_LIBRE < 0, 'DIAS_LIBRE'] = 0
#The individual is still on jail
df_mj.loc[df_mj['DIAS_LIBRE'].isnull(), 'DIAS_LIBRE'] = 0

#Find the last date the criminal went out the jail, so that these observations are marked as censored
last_df = df_mj[['INTERNOEN', 'FECHA_INGRESO']].groupby('INTERNOEN').apply(lambda x: x.sort_values('FECHA_INGRESO', ascending = False).head(1)).reset_index(drop = True)
#Censored
last_df['CENSURADO_LIBRES'] = 0
df_mj = df_mj.merge(last_df, on = ['INTERNOEN', 'FECHA_INGRESO'], how = 'left')
#Event
df_mj.loc[df_mj['CENSURADO_LIBRES'].isnull(), 'CENSURADO_LIBRES'] = 1
#All criminals that haven't got out of jail yet have zero days out and they are not censored.
df_mj.loc[df_mj['FECHA_SALIDA'].isnull(), 'CENSURADO_LIBRES'] = 1
#Turned censored variables to integers instead of float
df_mj['CENSURADO_LIBRES'] = df_mj['CENSURADO_LIBRES'].astype('int64')

#We create a variable to count the amount of times the individual re-entered in jail
df_mj = df_mj.merge(df_mj.drop_duplicates(['INTERNOEN', 'FECHA_INGRESO']).groupby(['INTERNOEN']).size().reset_index(name = 'NUMERO_REINCIDENCIAS'), on = 'INTERNOEN', how = 'left')

#We dropped SITUACION_JURIDICA and REINCIDENTE as both columns are constants
df_mj = df_mj.drop(columns = ['SITUACION_JURIDICA', 'REINCIDENTE'])

In [21]:
df_km = df_mj[['INTERNOEN', 'FECHA_INGRESO', 'DIAS_LIBRE', 'CENSURADO_LIBRES', 'ANO_INGRESO_INT', 'NUMERO_REINCIDENCIAS']].groupby('INTERNOEN').apply(lambda x: x.sort_values('FECHA_INGRESO', ascending = False).tail(1)).reset_index(drop = True)

In [22]:
A = df_mj[['INTERNOEN', 'FECHA_INGRESO']].apply(lambda x: x['INTERNOEN'] +  str(x['FECHA_INGRESO']), axis = 1)
B = df_km[['INTERNOEN', 'FECHA_INGRESO']].apply(lambda x: x['INTERNOEN'] + str(x['FECHA_INGRESO']), axis = 1)

diff = set(A).difference(set(B))
where_diff = A.isin(diff)

df_kmkm = df_mj.loc[where_diff, ['INTERNOEN', 'FECHA_INGRESO', 'DIAS_LIBRE', 'CENSURADO_LIBRES', 'ANO_INGRESO_INT', 'NUMERO_REINCIDENCIAS']].groupby('INTERNOEN').apply(lambda x: x.sort_values('FECHA_INGRESO', ascending = False).tail(1)).reset_index(drop = True)

C = df_kmkm[['INTERNOEN', 'FECHA_INGRESO']].apply(lambda x: x['INTERNOEN'] + str(x['FECHA_INGRESO']), axis = 1)

diff = diff.difference(set(C))
where_diff = A.isin(diff)

df_kmkmkm = df_mj.loc[where_diff, ['INTERNOEN', 'FECHA_INGRESO', 'DIAS_LIBRE', 'CENSURADO_LIBRES', 'ANO_INGRESO_INT', 'NUMERO_REINCIDENCIAS']].groupby('INTERNOEN').apply(lambda x: x.sort_values('FECHA_INGRESO', ascending = False).tail(1)).reset_index(drop = True)

D = df_kmkmkm[['INTERNOEN', 'FECHA_INGRESO']].apply(lambda x: x['INTERNOEN'] + str(x['FECHA_INGRESO']), axis = 1)

diff = diff.difference(set(D))
where_diff = A.isin(diff)

df_kmkmkmkm = df_mj.loc[where_diff, ['INTERNOEN', 'FECHA_INGRESO', 'DIAS_LIBRE', 'CENSURADO_LIBRES', 'ANO_INGRESO_INT', 'NUMERO_REINCIDENCIAS']].groupby('INTERNOEN').apply(lambda x: x.sort_values('FECHA_INGRESO', ascending = False).tail(1)).reset_index(drop = True)

E = df_kmkmkmkm[['INTERNOEN', 'FECHA_INGRESO']].apply(lambda x: x['INTERNOEN'] + str(x['FECHA_INGRESO']), axis = 1)

diff = diff.difference(set(E))
where_diff = A.isin(diff)

df_kmkmkmkmkm = df_mj.loc[where_diff, ['INTERNOEN', 'FECHA_INGRESO', 'DIAS_LIBRE', 'CENSURADO_LIBRES', 'ANO_INGRESO_INT', 'NUMERO_REINCIDENCIAS']].groupby('INTERNOEN').apply(lambda x: x.sort_values('FECHA_INGRESO', ascending = False).tail(1)).reset_index(drop = True)

In [23]:
fig = go.Figure()

for i in [0, 1]:
    kmf = KaplanMeierFitter()
    kmf.fit(df_km.loc[df_km['NUMERO_REINCIDENCIAS']>i,'DIAS_LIBRE'], df_km.loc[df_km['NUMERO_REINCIDENCIAS']>i, 'CENSURADO_LIBRES'])
    
    if i == 0:
        name= 'Días fuera de la cárcel (95% IC)'
        fillcolor='rgba(0,176,246,0.2)'
        line_color='rgba(255,255,255,0)' 
        line_color_l='rgb(0,176,246)'
    else:
        name = 'Días fuera de la cárcel sólo con reincidentes (95% IC)'
        fillcolor='rgba(231,107,243,0.2)'
        line_color='rgba(255,255,255,0)'
        line_color_l='rgb(231,107,243)'

    df = kmf.survival_function_.reset_index()
    df.columns = ['Dias', 'Probabilidad de pasar más días afuera']

    df_interval = kmf.confidence_interval_survival_function_.reset_index()
    df_interval.columns = ['Dias', 'lwr', 'upr']

    fig.add_trace(go.Scatter(
        x=list(df_interval.Dias)+list(df_interval.Dias)[::-1],
        y=list(df_interval.upr)+list(df_interval.lwr)[::-1],
        fill='toself',
        fillcolor=fillcolor,
        line_color=line_color,
        showlegend=False,
        name=name,
    ))
    fig.add_trace(go.Scatter(
        x=df['Dias'],
        y=df['Probabilidad de pasar más días afuera'],
        line_color=line_color_l,
        name=name,
    ))

fig.update_layout(
    xaxis_title ="Días",
    yaxis_title = "P(t > T)",
    title = 'Días entre la primera y segunda reincidencia',
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="#7f7f7f"
    )
)

fig.update_traces(mode='lines')
fig.show()

In [24]:
fig = go.Figure()

for i in [0, 2]:
    kmf = KaplanMeierFitter()
    kmf.fit(df_kmkm.loc[df_kmkm['NUMERO_REINCIDENCIAS']>i,'DIAS_LIBRE'], df_kmkm.loc[df_kmkm['NUMERO_REINCIDENCIAS']>i, 'CENSURADO_LIBRES'])
    
    if i == 0:
        name= 'Días fuera de la cárcel (95% IC)'
        fillcolor='rgba(0,176,246,0.2)'
        line_color='rgba(255,255,255,0)' 
        line_color_l='rgb(0,176,246)'
    else:
        name = 'Días fuera de la cárcel sólo con reincidentes (95% IC)'
        fillcolor='rgba(231,107,243,0.2)'
        line_color='rgba(255,255,255,0)'
        line_color_l='rgb(231,107,243)'

    df = kmf.survival_function_.reset_index()
    df.columns = ['Dias', 'Probabilidad de pasar más días afuera']

    df_interval = kmf.confidence_interval_survival_function_.reset_index()
    df_interval.columns = ['Dias', 'lwr', 'upr']

    fig.add_trace(go.Scatter(
        x=list(df_interval.Dias)+list(df_interval.Dias)[::-1],
        y=list(df_interval.upr)+list(df_interval.lwr)[::-1],
        fill='toself',
        fillcolor=fillcolor,
        line_color=line_color,
        showlegend=False,
        name=name,
    ))
    fig.add_trace(go.Scatter(
        x=df['Dias'],
        y=df['Probabilidad de pasar más días afuera'],
        line_color=line_color_l,
        name=name,
    ))

fig.update_layout(
    xaxis_title ="Días",
    yaxis_title = "P(t > T)",
    title = 'Días entre la segunda y tercera reincidencia',
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="#7f7f7f"
    )
)

fig.update_traces(mode='lines')
fig.show()

In [25]:
fig = go.Figure()

for i in [0, 3]:
    kmf = KaplanMeierFitter()
    kmf.fit(df_kmkmkm.loc[df_kmkmkm['NUMERO_REINCIDENCIAS']>i,'DIAS_LIBRE'], df_kmkmkm.loc[df_kmkmkm['NUMERO_REINCIDENCIAS']>i, 'CENSURADO_LIBRES'])
    
    if i == 0:
        name= 'Días fuera de la cárcel (95% IC)'
        fillcolor='rgba(0,176,246,0.2)'
        line_color='rgba(255,255,255,0)' 
        line_color_l='rgb(0,176,246)'
    else:
        name = 'Días fuera de la cárcel sólo con reincidentes (95% IC)'
        fillcolor='rgba(231,107,243,0.2)'
        line_color='rgba(255,255,255,0)'
        line_color_l='rgb(231,107,243)'

    df = kmf.survival_function_.reset_index()
    df.columns = ['Dias', 'Probabilidad de pasar más días afuera']

    df_interval = kmf.confidence_interval_survival_function_.reset_index()
    df_interval.columns = ['Dias', 'lwr', 'upr']

    fig.add_trace(go.Scatter(
        x=list(df_interval.Dias)+list(df_interval.Dias)[::-1],
        y=list(df_interval.upr)+list(df_interval.lwr)[::-1],
        fill='toself',
        fillcolor=fillcolor,
        line_color=line_color,
        showlegend=False,
        name=name,
    ))
    fig.add_trace(go.Scatter(
        x=df['Dias'],
        y=df['Probabilidad de pasar más días afuera'],
        line_color=line_color_l,
        name=name,
    ))

fig.update_layout(
    xaxis_title ="Días",
    yaxis_title = "P(t > T)",
    title = 'Días entre la tercera y cuarta reincidencia',
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="#7f7f7f"
    )
)

fig.update_traces(mode='lines')
fig.show()

In [26]:
fig = go.Figure()

for i in [0, 4]:
    kmf = KaplanMeierFitter()
    kmf.fit(df_kmkmkm.loc[df_kmkmkm['NUMERO_REINCIDENCIAS']>i,'DIAS_LIBRE'], df_kmkmkm.loc[df_kmkmkm['NUMERO_REINCIDENCIAS']>i, 'CENSURADO_LIBRES'])
    
    if i == 0:
        name= 'Días fuera de la cárcel (95% IC)'
        fillcolor='rgba(0,176,246,0.2)'
        line_color='rgba(255,255,255,0)' 
        line_color_l='rgb(0,176,246)'
    else:
        name = 'Días fuera de la cárcel sólo con reincidentes (95% IC)'
        fillcolor='rgba(231,107,243,0.2)'
        line_color='rgba(255,255,255,0)'
        line_color_l='rgb(231,107,243)'

    df = kmf.survival_function_.reset_index()
    df.columns = ['Dias', 'Probabilidad de pasar más días afuera']

    df_interval = kmf.confidence_interval_survival_function_.reset_index()
    df_interval.columns = ['Dias', 'lwr', 'upr']

    fig.add_trace(go.Scatter(
        x=list(df_interval.Dias)+list(df_interval.Dias)[::-1],
        y=list(df_interval.upr)+list(df_interval.lwr)[::-1],
        fill='toself',
        fillcolor=fillcolor,
        line_color=line_color,
        showlegend=False,
        name=name,
    ))
    fig.add_trace(go.Scatter(
        x=df['Dias'],
        y=df['Probabilidad de pasar más días afuera'],
        line_color=line_color_l,
        name=name,
    ))

fig.update_layout(
    xaxis_title ="Días",
    yaxis_title = "P(t > T)",
    title = 'Días entre la cuarta y quinta reincidencia',
    font=dict(
        family="Courier New, monospace",
        size=18,
        color="#7f7f7f"
    )
)

fig.update_traces(mode='lines')
fig.show()